In [1]:
from __future__ import  division, print_function, absolute_import
import tensorflow as tf
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
import mne
import sklearn.cross_validation as cross_validation
from mne.io import RawArray
from mne.epochs import concatenate_epochs
from mne import create_info, find_events, Epochs
from mne.channels import read_custom_montage
from sklearn.pipeline import make_pipeline
from sklearn.linear_model import LogisticRegression
from sklearn.cross_validation import cross_val_score, LeaveOneLabelOut
from glob import glob
from mpl_toolkits.axes_grid1 import make_axes_locatable
from scipy.signal import welch
from mne import pick_types
from tensorflow.examples.tutorials.mnist import input_data
import os.path
import scipy.io as sio

##########################
# create MNE readable file 
##########################
def creat_mne_raw_object(fname):
    """Create a mne raw instance from csv file"""
    # Read EEG file
    data = pd.read_csv(fname)
    
    # get chanel names
    ch_names = list(data.columns[1:])
    
    # read EEG standard montage from mne
    montage = 'standard_1005'

    # events file
    ev_fname = fname.replace('_data','_events')
    # read event file
    events = pd.read_csv(ev_fname)
    events_names = events.columns[1:]
    events_data = np.array(events[events_names]).T
    
    # concatenate event file and data
    data = np.concatenate((1e-6*np.array(data[ch_names]).T,events_data))        
    
    # define channel type, the first is EEG, the last 6 are stimulations
    ch_type = ['eeg']*len(ch_names) + ['stim']*6
    
    # create and populate MNE info structure
    ch_names.extend(events_names)
    info = create_info(ch_names,sfreq=500.0,ch_types=ch_type,montage = montage)
    # info.set_montage(montage)
    #info['filename'] = fname
    
    # create raw object 
    raw = RawArray(data,info,verbose=False)
    return raw


/home/yaoxiaojian/anaconda3/lib/python3.7/site-packages/sklearn/cross_validation.py:41: DeprecationWarning: This module was deprecated in version 0.18 in favor of the model_selection module into which all the refactored classes and functions are moved. Also note that the interface of the new CV iterators are different from that of this module. This module will be removed in 0.20.
  "This module will be removed in 0.20.", DeprecationWarning)


In [2]:
####################################################################
# Data preprocessing, band_pass, event related 1.5s + 1.5s featuring
####################################################################
def data_gen(subjects):    
    X_train=[]
    y_train=[]
    n = 0

    for i in range(len(subjects)):
        n+=1
        subject = subjects[i]
        epochs_Replace_tot = []
        epochs_Replace_rest_tot = []
        epochs_HandStart_tot = []
        epochs_HandStart_rest_tot = []

        fnames =  glob('../train/subj%d_series*_data.csv' % (subject))

        y = []
        for i,fname in enumerate(fnames):

            # read data 
            raw = creat_mne_raw_object(fname)
            #raw.plot(block=True)
            # pick eeg signal
            picks = pick_types(raw.info,eeg=True)

            # Filter data for alpha frequency and beta band
            # Note that MNE implement a zero phase (filtfilt) filtering not compatible
            # with the rule of future data.
            raw.filter(7,35, picks=picks, method='iir', n_jobs=-1, verbose=False)

            #id = 'Replace'
            # get event posision corresponding to Replace
            events = find_events(raw,stim_channel='Replace', verbose=False)
            # epochs signal for 1.5 second before the movement
            epochs = Epochs(raw, events, {'during' : 1}, -2, -0.5, proj=False, picks=picks, baseline=None, preload=True, verbose=False)

            epochs_Replace_tot.append(epochs)


            # epochs signal for 1.5 second after the movement, this correspond to the 
            # rest period.
            epochs_rest = Epochs(raw, events, {'after' : 1}, 0.5, 2, proj=False, picks=picks, baseline=None, preload=True, verbose=False)

            # Workaround to be able to concatenate epochs
            epochs_rest.shift_time(-2.5, relative = True)

            epochs_Replace_rest_tot.append(epochs_rest)

            # id = 'HandStart'
            # get event posision corresponding to HandStart
            events = find_events(raw,stim_channel='HandStart', verbose=False)
            # epochs signal for 1.5 second before the movement
            epochs = Epochs(raw, events, {'during' : 1}, 0.5, 2, proj=False, picks=picks, baseline=None, preload=True, verbose=False)

            epochs_HandStart_tot.append(epochs)

            # epochs signal for 1.5 second after the movement, this correspond to the 
            # rest period.
            epochs_rest = Epochs(raw, events, {'before' : 1}, -2, -0.5, proj=False, picks=picks, baseline=None, preload=True, verbose=False)

            # Workaround to be able to concatenate epochs
            epochs_rest.shift_time(2.5, relative = True)

            epochs_HandStart_rest_tot.append(epochs_rest)


        epochs_Replace = concatenate_epochs(epochs_Replace_tot)
        epochs_Replace_rest = concatenate_epochs(epochs_Replace_rest_tot)
        epochs_HandStart = concatenate_epochs(epochs_HandStart_tot)
        epochs_HandStart_rest = concatenate_epochs(epochs_HandStart_rest_tot)
    
        # epochs.plot_psd( fmin=2.,fmax=40.,average=True, spatial_colors=True)
        # epochs_rest.plot_psd( fmin=2.,fmax=40.,average=True, spatial_colors=True)

        # epochs.plot_psd_topomap(ch_type='eeg',normalize=True)
        # epochs_rest.plot_psd_topomap(ch_type='eeg',normalize=True)

        #get data 
        X_Replace = epochs_Replace.get_data()
        X_Replace_rest = epochs_Replace_rest.get_data()
        X_Replace_var = np.concatenate((X_Replace,X_Replace_rest),axis=1)

        X_HandStart = epochs_HandStart.get_data()
        X_HandStart_rest = epochs_HandStart_rest.get_data()
        X_HandStart_var = np.concatenate((X_HandStart_rest,X_HandStart),axis=1)

        X = np.concatenate((X_Replace_var,X_HandStart_var),axis=0)
        #y = np.array(y)
        print ("subject",subject,X.shape)

        if n == 1:
            X_train = X

        else:
            X_train=np.append(X_train,X,axis =0)

        y = np.concatenate((np.ones(260),np.zeros(260)),axis=0)
        y_train = np.concatenate((y_train,y),axis=0)
        print ("data stack shape:",X_train.shape,y_train.shape)

    # generate feature dataset for next process, it contains (HandStar,rest),(Replace,rest) 
    X_train = np.array(X_train)
    y_train = np.array(y_train)
    print ('return data shape: ',X_train.shape,y_train.shape)
    return (X_train, y_train)


In [3]:
for j in range(1,13):
    train_subject = [k for k in range(1,13) if k != j]
    test_subject = [j]
    train_X,train_y = data_gen(train_subject)
    test_X,test_y = data_gen(test_subject)
    
    idx = list(range(len(train_y)))
    np.random.shuffle(idx)
    train_X = train_X[idx]
    train_y = train_y[idx]
    sio.savemat('/home/yaoxiaojian/Desktop/kaggle/EEG/TACR_independent_2-class/T-set_sub'+str(j)+'.mat', {"train_x": train_X, "train_y": train_y, "test_x": test_X, "test_y": test_y})



DigMontage is a superset of info. 311 in DigMontage will be ignored. The ignored channels are: {'FFT10', 'AFp4h', 'OIz', 'F5', 'AFF2', 'AFF3h', 'AFp6h', 'AF3', 'PO1h', 'FFC6', 'FCCz', 'FCC1h', 'TPP8', 'AFp10', 'AFp10h', 'CCP4', 'TP7', 'FC2h', 'FCC6h', 'T9', 'AFF1h', 'PO3', 'PO7h', 'P1', 'AF3h', 'AFF3', 'Iz', 'CPPz', 'T3', 'A2', 'FCC5', 'CP3h', 'F1', 'CCP5', 'C1h', 'FC4', 'AFp2h', 'FC3', 'T10h', 'FCC2', 'TP10h', 'T9h', 'C6h', 'CP4h', 'T8h', 'FT7', 'AFp9h', 'AFp8', 'AFp4', 'OI1', 'AF4h', 'FT8h', 'F2h', 'C2h', 'AF10', 'CCP6', 'TTP9', 'C5h', 'CCP6h', 'AF1h', 'Fpz', 'AFFz', 'PPO9', 'POO2', 'AFp1h', 'AFF6', 'FCC3h', 'P10', 'AF2', 'FFT7h', 'AFF8h', 'POO6h', 'POO8', 'AF1', 'AF7', 'CCP3h', 'PPO5', 'AF9h', 'O2h', 'AFF8', 'CCP3', 'AF2h', 'FFC5', 'AFF7', 'FFC4', 'OI1h', 'CPP2h', 'FT7h', 'T5', 'AFF6h', 'FC1h', 'P9h', 'POO6', 'F6h', 'POO4h', 'POO4', 'PPO3', 'FCC4', 'FCC4h', 'PO6', 'C3h', 'CP6h', 'Fp1h', 'M1', 'AFp3h', 'PPO2', 'PPO4h', 'TPP7', 'FC5h', 'PO8h', 'CPP5h', 'CPP3', 'P4h', 'POO10', 'AF5h', 

<ipython-input-1-deb7d153ad1a>:52: RuntimeWarning: 1 channel names are too long, have been truncated to 15 characters:
['BothStartLoadPhase']
  info = create_info(ch_names,sfreq=500.0,ch_types=ch_type,montage = montage)
/home/yaoxiaojian/anaconda3/lib/python3.7/site-packages/scipy/signal/_arraytools.py:45: FutureWarning: Using a non-tuple sequence for multidimensional indexing is deprecated; use `arr[tuple(seq)]` instead of `arr[seq]`. In the future this will be interpreted as an array index, `arr[np.array(seq)]`, which will result either in an error or a different result.
  b = a[a_slice]
/home/yaoxiaojian/anaconda3/lib/python3.7/site-packages/scipy/signal/_arraytools.py:45: FutureWarning: Using a non-tuple sequence for multidimensional indexing is deprecated; use `arr[tuple(seq)]` instead of `arr[seq]`. In the future this will be interpreted as an array index, `arr[np.array(seq)]`, which will result either in an error or a different result.
  b = a[a_slice]
/home/yaoxiaojian/anaconda

DigMontage is a superset of info. 311 in DigMontage will be ignored. The ignored channels are: {'FFT10', 'AFp4h', 'OIz', 'F5', 'AFF2', 'AFF3h', 'AFp6h', 'AF3', 'PO1h', 'FFC6', 'FCCz', 'FCC1h', 'TPP8', 'AFp10', 'AFp10h', 'CCP4', 'TP7', 'FC2h', 'FCC6h', 'T9', 'AFF1h', 'PO3', 'PO7h', 'P1', 'AF3h', 'AFF3', 'Iz', 'CPPz', 'T3', 'A2', 'FCC5', 'CP3h', 'F1', 'CCP5', 'C1h', 'FC4', 'AFp2h', 'FC3', 'T10h', 'FCC2', 'TP10h', 'T9h', 'C6h', 'CP4h', 'T8h', 'FT7', 'AFp9h', 'AFp8', 'AFp4', 'OI1', 'AF4h', 'FT8h', 'F2h', 'C2h', 'AF10', 'CCP6', 'TTP9', 'C5h', 'CCP6h', 'AF1h', 'Fpz', 'AFFz', 'PPO9', 'POO2', 'AFp1h', 'AFF6', 'FCC3h', 'P10', 'AF2', 'FFT7h', 'AFF8h', 'POO6h', 'POO8', 'AF1', 'AF7', 'CCP3h', 'PPO5', 'AF9h', 'O2h', 'AFF8', 'CCP3', 'AF2h', 'FFC5', 'AFF7', 'FFC4', 'OI1h', 'CPP2h', 'FT7h', 'T5', 'AFF6h', 'FC1h', 'P9h', 'POO6', 'F6h', 'POO4h', 'POO4', 'PPO3', 'FCC4', 'FCC4h', 'PO6', 'C3h', 'CP6h', 'Fp1h', 'M1', 'AFp3h', 'PPO2', 'PPO4h', 'TPP7', 'FC5h', 'PO8h', 'CPP5h', 'CPP3', 'P4h', 'POO10', 'AF5h', 

<ipython-input-1-deb7d153ad1a>:52: RuntimeWarning: 1 channel names are too long, have been truncated to 15 characters:
['BothStartLoadPhase']
  info = create_info(ch_names,sfreq=500.0,ch_types=ch_type,montage = montage)
/home/yaoxiaojian/anaconda3/lib/python3.7/site-packages/scipy/signal/_arraytools.py:45: FutureWarning: Using a non-tuple sequence for multidimensional indexing is deprecated; use `arr[tuple(seq)]` instead of `arr[seq]`. In the future this will be interpreted as an array index, `arr[np.array(seq)]`, which will result either in an error or a different result.
  b = a[a_slice]
/home/yaoxiaojian/anaconda3/lib/python3.7/site-packages/scipy/signal/_arraytools.py:45: FutureWarning: Using a non-tuple sequence for multidimensional indexing is deprecated; use `arr[tuple(seq)]` instead of `arr[seq]`. In the future this will be interpreted as an array index, `arr[np.array(seq)]`, which will result either in an error or a different result.
  b = a[a_slice]
/home/yaoxiaojian/anaconda

DigMontage is a superset of info. 311 in DigMontage will be ignored. The ignored channels are: {'FFT10', 'AFp4h', 'OIz', 'F5', 'AFF2', 'AFF3h', 'AFp6h', 'AF3', 'PO1h', 'FFC6', 'FCCz', 'FCC1h', 'TPP8', 'AFp10', 'AFp10h', 'CCP4', 'TP7', 'FC2h', 'FCC6h', 'T9', 'AFF1h', 'PO3', 'PO7h', 'P1', 'AF3h', 'AFF3', 'Iz', 'CPPz', 'T3', 'A2', 'FCC5', 'CP3h', 'F1', 'CCP5', 'C1h', 'FC4', 'AFp2h', 'FC3', 'T10h', 'FCC2', 'TP10h', 'T9h', 'C6h', 'CP4h', 'T8h', 'FT7', 'AFp9h', 'AFp8', 'AFp4', 'OI1', 'AF4h', 'FT8h', 'F2h', 'C2h', 'AF10', 'CCP6', 'TTP9', 'C5h', 'CCP6h', 'AF1h', 'Fpz', 'AFFz', 'PPO9', 'POO2', 'AFp1h', 'AFF6', 'FCC3h', 'P10', 'AF2', 'FFT7h', 'AFF8h', 'POO6h', 'POO8', 'AF1', 'AF7', 'CCP3h', 'PPO5', 'AF9h', 'O2h', 'AFF8', 'CCP3', 'AF2h', 'FFC5', 'AFF7', 'FFC4', 'OI1h', 'CPP2h', 'FT7h', 'T5', 'AFF6h', 'FC1h', 'P9h', 'POO6', 'F6h', 'POO4h', 'POO4', 'PPO3', 'FCC4', 'FCC4h', 'PO6', 'C3h', 'CP6h', 'Fp1h', 'M1', 'AFp3h', 'PPO2', 'PPO4h', 'TPP7', 'FC5h', 'PO8h', 'CPP5h', 'CPP3', 'P4h', 'POO10', 'AF5h', 

...

DigMontage is a superset of info. 311 in DigMontage will be ignored. The ignored channels are: {'FFT10', 'AFp4h', 'OIz', 'F5', 'AFF2', 'AFF3h', 'AFp6h', 'AF3', 'PO1h', 'FFC6', 'FCCz', 'FCC1h', 'TPP8', 'AFp10', 'AFp10h', 'CCP4', 'TP7', 'FC2h', 'FCC6h', 'T9', 'AFF1h', 'PO3', 'PO7h', 'P1', 'AF3h', 'AFF3', 'Iz', 'CPPz', 'T3', 'A2', 'FCC5', 'CP3h', 'F1', 'CCP5', 'C1h', 'FC4', 'AFp2h', 'FC3', 'T10h', 'FCC2', 'TP10h', 'T9h', 'C6h', 'CP4h', 'T8h', 'FT7', 'AFp9h', 'AFp8', 'AFp4', 'OI1', 'AF4h', 'FT8h', 'F2h', 'C2h', 'AF10', 'CCP6', 'TTP9', 'C5h', 'CCP6h', 'AF1h', 'Fpz', 'AFFz', 'PPO9', 'POO2', 'AFp1h', 'AFF6', 'FCC3h', 'P10', 'AF2', 'FFT7h', 'AFF8h', 'POO6h', 'POO8', 'AF1', 'AF7', 'CCP3h', 'PPO5', 'AF9h', 'O2h', 'AFF8', 'CCP3', 'AF2h', 'FFC5', 'AFF7', 'FFC4', 'OI1h', 'CPP2h', 'FT7h', 'T5', 'AFF6h', 'FC1h', 'P9h', 'POO6', 'F6h', 'POO4h', 'POO4', 'PPO3', 'FCC4', 'FCC4h', 'PO6', 'C3h', 'CP6h', 'Fp1h', 'M1', 'AFp3h', 'PPO2', 'PPO4h', 'TPP7', 'FC5h', 'PO8h', 'CPP5h', 'CPP3', 'P4h', 'POO10', 'AF5h', 

<ipython-input-1-deb7d153ad1a>:52: RuntimeWarning: 1 channel names are too long, have been truncated to 15 characters:
['BothStartLoadPhase']
  info = create_info(ch_names,sfreq=500.0,ch_types=ch_type,montage = montage)
/home/yaoxiaojian/anaconda3/lib/python3.7/site-packages/scipy/signal/_arraytools.py:45: FutureWarning: Using a non-tuple sequence for multidimensional indexing is deprecated; use `arr[tuple(seq)]` instead of `arr[seq]`. In the future this will be interpreted as an array index, `arr[np.array(seq)]`, which will result either in an error or a different result.
  b = a[a_slice]
/home/yaoxiaojian/anaconda3/lib/python3.7/site-packages/scipy/signal/_arraytools.py:45: FutureWarning: Using a non-tuple sequence for multidimensional indexing is deprecated; use `arr[tuple(seq)]` instead of `arr[seq]`. In the future this will be interpreted as an array index, `arr[np.array(seq)]`, which will result either in an error or a different result.
  b = a[a_slice]
/home/yaoxiaojian/anaconda

DigMontage is a superset of info. 311 in DigMontage will be ignored. The ignored channels are: {'FFT10', 'AFp4h', 'OIz', 'F5', 'AFF2', 'AFF3h', 'AFp6h', 'AF3', 'PO1h', 'FFC6', 'FCCz', 'FCC1h', 'TPP8', 'AFp10', 'AFp10h', 'CCP4', 'TP7', 'FC2h', 'FCC6h', 'T9', 'AFF1h', 'PO3', 'PO7h', 'P1', 'AF3h', 'AFF3', 'Iz', 'CPPz', 'T3', 'A2', 'FCC5', 'CP3h', 'F1', 'CCP5', 'C1h', 'FC4', 'AFp2h', 'FC3', 'T10h', 'FCC2', 'TP10h', 'T9h', 'C6h', 'CP4h', 'T8h', 'FT7', 'AFp9h', 'AFp8', 'AFp4', 'OI1', 'AF4h', 'FT8h', 'F2h', 'C2h', 'AF10', 'CCP6', 'TTP9', 'C5h', 'CCP6h', 'AF1h', 'Fpz', 'AFFz', 'PPO9', 'POO2', 'AFp1h', 'AFF6', 'FCC3h', 'P10', 'AF2', 'FFT7h', 'AFF8h', 'POO6h', 'POO8', 'AF1', 'AF7', 'CCP3h', 'PPO5', 'AF9h', 'O2h', 'AFF8', 'CCP3', 'AF2h', 'FFC5', 'AFF7', 'FFC4', 'OI1h', 'CPP2h', 'FT7h', 'T5', 'AFF6h', 'FC1h', 'P9h', 'POO6', 'F6h', 'POO4h', 'POO4', 'PPO3', 'FCC4', 'FCC4h', 'PO6', 'C3h', 'CP6h', 'Fp1h', 'M1', 'AFp3h', 'PPO2', 'PPO4h', 'TPP7', 'FC5h', 'PO8h', 'CPP5h', 'CPP3', 'P4h', 'POO10', 'AF5h', 

<ipython-input-1-deb7d153ad1a>:52: RuntimeWarning: 1 channel names are too long, have been truncated to 15 characters:
['BothStartLoadPhase']
  info = create_info(ch_names,sfreq=500.0,ch_types=ch_type,montage = montage)
/home/yaoxiaojian/anaconda3/lib/python3.7/site-packages/scipy/signal/_arraytools.py:45: FutureWarning: Using a non-tuple sequence for multidimensional indexing is deprecated; use `arr[tuple(seq)]` instead of `arr[seq]`. In the future this will be interpreted as an array index, `arr[np.array(seq)]`, which will result either in an error or a different result.
  b = a[a_slice]
/home/yaoxiaojian/anaconda3/lib/python3.7/site-packages/scipy/signal/_arraytools.py:45: FutureWarning: Using a non-tuple sequence for multidimensional indexing is deprecated; use `arr[tuple(seq)]` instead of `arr[seq]`. In the future this will be interpreted as an array index, `arr[np.array(seq)]`, which will result either in an error or a different result.
  b = a[a_slice]
/home/yaoxiaojian/anaconda

subject 12 (520, 64, 751)
data stack shape: (520, 64, 751) (520,)
return data shape:  (520, 64, 751) (520,)
